In [1]:
import os

os.chdir('/Users/gabriele/PycharmProjects/RecSys')
from Utils.utils import create_URM, create_ICM, combine_matrices, create_submission, write_submission
from src.Evaluation.Evaluator import EvaluatorHoldout
from src.Evaluation.K_FoldEvaluator import K_FoldEvaluator
from src.Data_manager.split_functions.split_train_validation_random_holdout import split_train_in_two_percentage_global_sample
##NON-PERSONALIZED
from src.Recommenders.Base.NonPersonalizedRecommender import TopPop

#KNN
from src.Recommenders.KNN.UserKNNCFRecommender import UserKNNCFRecommender
from src.Recommenders.KNN.ItemKNNCFRecommender import ItemKNNCFRecommender
from src.Recommenders.KNN.ItemKNNCBFRecommender import ItemKNNCBFRecommender
from src.Recommenders.KNN.ItemKNN_CFCBF_Hybrid_Recommender import ItemKNN_CFCBF_Hybrid_Recommender
from src.Recommenders.KNN.ItemKNNSimilarityHybridRecommender import ItemKNNSimilarityHybridRecommender

#MATRIX-FACTORIZATION
from src.Recommenders.SLIM.Cython.SLIM_BPR_Cython import SLIM_BPR_Cython
from src.Recommenders.SLIM.SLIMElasticNetRecommender import MultiThreadSLIM_SLIMElasticNetRecommender
from src.Recommenders.MatrixFactorization.Cython.MatrixFactorization_Cython import MatrixFactorization_BPR_Cython, MatrixFactorization_FunkSVD_Cython, MatrixFactorization_AsySVD_Cython
from src.Recommenders.MatrixFactorization.PureSVDRecommender import PureSVDRecommender
from src.Recommenders.MatrixFactorization.IALSRecommenderLinear import IALSRecommender
from src.Recommenders.MatrixFactorization.NMFRecommender import NMFRecommender

#GRAPHIC-BASED
from src.Recommenders.GraphBased.P3alphaRecommender import P3alphaRecommender
from src.Recommenders.GraphBased.RP3betaRecommender import RP3betaRecommender

#HYBRID
from src.Hybrids.MergingModelsByScores import MergeTwoModelsByScores, MergeThreeModelsByScores

In [2]:
##CREATION OF MATRICES AND SPLITTING IN TRAIN-TEST-VALIDATION
URM = create_URM()
ICM = create_ICM()

URM_train_list=[]
URM_validation_list=[]
evaluator_list=[]

In [3]:
for k in range(3):
    URM_train,URM_validation = split_train_in_two_percentage_global_sample(URM, train_percentage=0.8)
    URM_train_list.append(URM_train)
    URM_validation_list.append(URM_validation)
    evaluator_list.append(EvaluatorHoldout(URM_validation, cutoff_list=[10],verbose=False))

In [4]:
URM_combined_list=[]
for URM_i in URM_train_list:
    URM_combined_list.append(combine_matrices(ICM=ICM,URM=URM_i))

In [5]:
from bayes_opt import BayesianOptimization

In [6]:

slime_recommenders=[]


for i in range(len(URM_train_list)):
    slime_recommenders.append(MultiThreadSLIM_SLIMElasticNetRecommender(URM_train=URM_combined_list[i]))

In [7]:
tuning_params = {
    "topK":(450,600),
    "l1_ratio":(0.00001,0.001),
    "alpha":(0.01,0.1)
}

In [8]:

def BO_function(topK,l1_ratio,alpha):
    MAP = 0
    k = 3
    cutoff=10
    for i in range(len(slime_recommenders)):
        slime_recommenders[i].fit(topK,l1_ratio,alpha)
        result_df, _ = evaluator_list[i].evaluateRecommender(slime_recommenders[i])
        MAP += result_df.loc[cutoff]["MAP"]
        
    return MAP/k


In [10]:
optimizer = BayesianOptimization(f=BO_function,
                                pbounds=tuning_params,
                                verbose=3,
                                random_state=3)

optimizer.maximize(init_points=30,n_iter=30)


|   iter    |  target   |   alpha   | l1_ratio  |   topK    |
-------------------------------------------------------------



 19%|███████▎                              | 3496/18059 [00:41<02:35, 93.85it/s]


 37%|█████████████▉                        | 6600/18059 [01:19<02:36, 73.29it/s]


 54%|████████████████████▍                 | 9704/18059 [01:57<01:42, 81.43it/s]


 71%|██████████████████████████▏          | 12808/18059 [02:37<01:11, 73.41it/s]


...

 31%|███████████▉                          | 5672/18059 [01:09<02:39, 77.43it/s]

 32%|████████████                          | 5704/18059 [01:09<02:20, 88.11it/s]

 32%|████████████                          | 5736/18059 [01:10<02:35, 79.35it/s]

 32%|████████████▏                         | 5768/18059 [01:10<02:18, 88.97it/s]

 32%|████████████▏                         | 5800/18059 [01:11<02:32, 80.45it/s]

 32%|████████████▎                         | 5832/18059 [01:11<02:16, 89.33it/s]

 32%|████████████▎                         | 5864/18059 [01:11<02:30, 81.15it/s]

 33%|████████████▍                         | 5896/18059 [01:12<02:17, 88.53it/s]

 33%|████████████▍                         | 5928/18059 [01:12<02:29, 81.27it/s]

 33%|████████████▌                         | 5960/18059 [01:12<02:17, 87.72it/s]

 33%|████████████▌                         | 5992/18059 [01:13<02:27, 81.79it/s]

 33%|████████████▋                         | 6024/18059 [01:13<02:17, 87.79it/s]

 34%|███████████

 50%|██████████████████▊                   | 8968/18059 [01:50<01:49, 83.04it/s]

 50%|███████████████████                   | 9032/18059 [01:51<01:48, 83.16it/s]

 50%|███████████████████▏                  | 9096/18059 [01:52<01:47, 83.42it/s]

 51%|███████████████████▎                  | 9160/18059 [01:53<01:46, 83.46it/s]

 51%|███████████████████▍                  | 9224/18059 [01:54<01:45, 83.69it/s]

 51%|███████████████████▌                  | 9288/18059 [01:54<01:44, 84.16it/s]

 52%|███████████████████▋                  | 9352/18059 [01:55<01:43, 84.32it/s]

 52%|███████████████████▊                  | 9416/18059 [01:56<01:42, 84.16it/s]

 52%|███████████████████▉                  | 9480/18059 [01:57<01:42, 83.97it/s]

 53%|████████████████████                  | 9544/18059 [01:57<01:41, 84.12it/s]

 53%|████████████████████▏                 | 9576/18059 [01:57<01:27, 96.45it/s]

 53%|████████████████████▏                 | 9608/18059 [01:58<01:44, 80.60it/s]

 53%|███████████

 68%|█████████████████████████            | 12232/18059 [02:30<01:09, 84.39it/s]

 68%|█████████████████████████▏           | 12264/18059 [02:31<01:21, 70.79it/s]

 68%|█████████████████████████▏           | 12296/18059 [02:31<01:08, 84.74it/s]

 68%|█████████████████████████▎           | 12328/18059 [02:32<01:21, 70.17it/s]

 68%|█████████████████████████▎           | 12360/18059 [02:32<01:07, 84.28it/s]

 69%|█████████████████████████▍           | 12392/18059 [02:33<01:21, 69.48it/s]

 69%|█████████████████████████▍           | 12424/18059 [02:33<01:07, 84.02it/s]

 69%|█████████████████████████▌           | 12456/18059 [02:33<01:21, 69.08it/s]

 69%|█████████████████████████▌           | 12488/18059 [02:34<01:06, 84.05it/s]

 69%|█████████████████████████▋           | 12520/18059 [02:34<01:20, 68.96it/s]

 70%|█████████████████████████▋           | 12552/18059 [02:34<01:05, 84.12it/s]

 70%|█████████████████████████▊           | 12584/18059 [02:35<01:18, 70.10it/s]

 70%|███████████

 88%|████████████████████████████████▋    | 15944/18059 [03:15<00:24, 86.48it/s]

 88%|████████████████████████████████▋    | 15976/18059 [03:16<00:24, 85.08it/s]

 89%|████████████████████████████████▊    | 16008/18059 [03:16<00:23, 86.32it/s]

 89%|████████████████████████████████▊    | 16040/18059 [03:16<00:23, 86.91it/s]

 89%|████████████████████████████████▉    | 16072/18059 [03:17<00:23, 86.36it/s]

 89%|████████████████████████████████▉    | 16104/18059 [03:17<00:22, 86.59it/s]

 89%|█████████████████████████████████    | 16136/18059 [03:17<00:22, 85.65it/s]

 90%|█████████████████████████████████▏   | 16168/18059 [03:18<00:21, 86.47it/s]

 90%|█████████████████████████████████▏   | 16200/18059 [03:18<00:21, 84.75it/s]

 90%|█████████████████████████████████▎   | 16232/18059 [03:18<00:20, 87.01it/s]

 90%|█████████████████████████████████▎   | 16264/18059 [03:19<00:21, 84.16it/s]

 90%|█████████████████████████████████▍   | 16296/18059 [03:19<00:20, 87.68it/s]

 90%|███████████

|  60       |  0.001104 |  0.03782  |  0.000788 |  518.6    |


In [11]:
import json
with open("tuning_KFOLD/SLIM_Elasticnet/" + slime_recommenders[0].RECOMMENDER_NAME + "2_logs.json", 'w') as json_file:
    json.dump(optimizer.max, json_file)